In [26]:
import pandas as pd
import numpy as np
import time
import sklearn.preprocessing as sk
from sklearn import svm
from keras.models import Sequential
from keras.layers import *
from keras.optimizers import *

In [4]:
# A method to fix the API
def fixAPI(API):
    if API[0]=='5':
        API = '0'+API
    return API

In [5]:
# Reading the data
start = time.time()
production_data_train = pd.read_csv("production_data_train.csv",dtype={'API':str})
# production_data_test = pd.read_csv("production_data_test.csv",dtype={'API':str})
end = time.time()
print('ReadData',end-start)

ReadData 0.46202611923217773


In [6]:
# Fix api
start = time.time()
production_data_train["API"] = production_data_train["API"].apply(fixAPI)
end = time.time()
print('FixApi',end-start)

FixApi 0.06400346755981445


In [7]:
# Removing duplicates
start = time.time()
production_data_train = production_data_train.sort_values(['_LastUpdate'])
production_data_train.drop_duplicates(subset=['API','Year','Month'],keep='last',inplace=True)
end = time.time()
print('RemovingDuplicates',end-start)

RemovingDuplicates 0.44602537155151367


In [8]:
# Remove pre-peek month
start = time.time()
maxLiquid = production_data_train.groupby(['API'],as_index=False).agg({'Liquid':'max'})
maxDate = pd.merge(maxLiquid[['API','Liquid']],production_data_train[['API','Liquid','Year','Month']],on=['API','Liquid'],how='left')

max1 = maxDate.groupby(['API','Liquid'],as_index=False).agg({'Year':'min'})
maxDate = pd.merge(maxDate[['API','Liquid','Year','Month']],max1[['API','Liquid','Year']],on=['API','Liquid','Year'],how='right')
maxDate = maxDate.groupby(['API','Liquid','Year'],as_index=False).agg({'Month':'min'})

maxDate = maxDate[['API','Year','Month']]
maxDate = maxDate.rename(columns={"Year":"maxYear",'Month':'maxMonth'})
production_data_train = pd.merge(production_data_train,maxDate[['API','maxYear','maxMonth']],on='API')
production_data_train = production_data_train[((production_data_train['Year']-production_data_train['maxYear'])*12+production_data_train['Month']-production_data_train['maxMonth'])>=0]

end = time.time()
print('RemovePrePeekMonth',end-start)

RemovePrePeekMonth 0.41602396965026855


In [9]:
# Adding Index
start = time.time()
production_data_train["Index"] = (production_data_train["Year"]-production_data_train['maxYear'])*12+production_data_train["Month"]-production_data_train["maxMonth"]+1
end = time.time()
print('IndexColumn',end-start)

IndexColumn 0.06000328063964844


In [10]:
production_data_train

API  Year  Month  Liquid    Gas  RatioGasOil  Water  \
0       33053063590000  2015      6   10421  12311     1.181365   2717   
1       33053063590000  2015      7    9777  11254     1.151069   2399   
2       33053063590000  2015      8   10613  12188     1.148403   2742   
3       33053063590000  2015      9   13119  17739     1.352161   2903   
4       33053063590000  2015     10   10318  12979     1.257899   2286   
5       33053063590000  2015     11    8126   9642     1.186562   1795   
6       33053063590000  2016      3    6793   8367     1.231709   1803   
7       33053063590000  2016      4    7325  11139     1.520683   1798   
8       33053063590000  2016      5    7381  15601     2.113670   1975   
9       33053063590000  2015     12    7527   7570     1.005713   1679   
10      33053063590000  2015      5   14626  15988     1.093122   4213   
11      33053063590000  2015      4   18796  21796     1.159608   7255   
12      33053063590000  2016      1    7934   8823     1.112049   1943   
13      33053063590000  2016      6    5975  11362     1.901590   1610   
15      33053063590000  2016      8    5390   8475     1.572356   1417   
16      33053063590000  2016      9    4626   6954     1.503243   1223   
17      33053063590000  2016     10    3432   4814     1.402681    899   
18      33053063590000  2017      3    1624   1590     0.979064    366   
19      33053063590000  2017      4     829    941     1.135103    195   
20      33053063590000  2017      5    1912   1964     1.027197   2619   
21      33053063590000  2017      6    6338   7363     1.161723   2617   
22      33053063590000  2017      7    6182   7996     1.293433   2005   
23      33053063590000  2017      9    4864   6915     1.421669   1484   
24      33053063590000  2017     10    4617   6937     1.502491   1335   
25      33053063590000  2017     11    4185   6196     1.480526   1342   
26      33053063590000  2017      8    5345   7149     1.337512   1643   
27      33053063590000  2017     12    3770   5121     1.358355   1147   
28      33053063590000  2018      1    3194   3696     1.157170    977   
29      33053063590000  2016      2    7337  10581     1.442143   1783   
30      33053063590000  2016     12    3688   3998     1.084056   2066   
...                ...   ...    ...     ...    ...          ...    ...   
394033  42301324920100  2016     10    3155   6221     1.971791  22023   
394034  42301324920100  2016     11    2687   6382     2.375140  18719   
394035  42301324920100  2016      1    4073   4162     1.021851  22479   
394036  42301324920100  2017      1    2162   4021     1.859852  15072   
394037  42301324920100  2017      8    2487   4485     1.803378  19958   
394038  42301324920100  2017      3    3542   5806     1.639187  26627   
394039  42301324920100  2018      7    7432   9536     1.283100  66864   
394040  42301324920100  2018      6    4531   8700     1.920106  40840   
394041  42301324920100  2018      5    2387  10603     4.441977  21452   
394042  42301324920100  2018      4    3571   3083     0.863344  32145   
394043  42301324920100  2018      3    1759   2928     1.664582  15769   
394044  42301324920100  2018      2    4791   6731     1.404926  43147   
394045  42301324920100  2018      1    1974   3006     1.522796  16686   
394046  42301324920100  2017      2    1796   3636     2.024499  13498   
394047  42301324920100  2017     12    2772   4049     1.460678  23671   
394048  42301324920100  2017     10    1469   5380     3.662355  12596   
394049  42301324920100  2017      9    1007   2896     2.875869   7967   
394050  42301324920100  2015      9    8387  13538     1.614165  41875   
394051  42301324920100  2017      7    1421   2205     1.551724  11337   
394052  42301324920100  2017      6    2633   1986     0.754273  21004   
394053  42301324920100  2017      5    2645   4511     1.705482  19915   
394054  42301324920100  2017      4    1615   4372     2.707121  12083   
394055  42301324920100 

In [11]:
# Getting the training labels (3_yrs_cum_oil production)
temp = production_data_train[production_data_train["Index"]<=36]
y_train = temp.groupby("API").agg({'Liquid':'sum'})
y_train

Liquid
API                   
05001097720000   65412
05001097780100   84043
05001097800000   13471
05001097820000   12992
05001097830000   15195
05001098050100  176206
05001098450000  180189
05005071800000  126323
05005071890100   66150
05005071920000  186252
05005072090000  142882
05005072120000   62652
05005072140100   63836
05005072150100   99022
05005072170100  234552
05005072190100  264294
05005072210000  250013
05005072220000  102986
05005072250100  200616
05005072260000  217756
05123315730000   20563
05123331840000   17377
05123334240100   20788
05123349460000   91506
05123349600000   76262
05123349910100    7703
05123350610000   70095
05123350770000   91265
05123352460000   28831
05123352590000   51454
...                ...
49021211170000  180118
49021211180000  133436
49021211280000  142229
49021211310000  201533
49021211320000   87110
49021211460000   73927
49021211760000   31937
49021211780000  207008
49021211800000  236270
49021211820000  191163
49021212030000  146182
49021212280000  164647
49021212460000  222063
49021212470000  187938
49021212490000  236922
49021213620000   95972
49021213990000   90304
49021214000000   31496
49021214010000   41765
49021215910000   88956
49021217890000   63698
49021219480000  134031
49021221450000  161373
49021222690000  106619
49021222710000   71089
49021222940000  227454
49021222950000  211789
49021223030000  230485
49021226570000   26615
49021226580100   31585

[7844 rows x 1 columns]

In [12]:
# reading the features CSVs
Harmony_data = pd.read_csv("Harmony_data.csv",dtype={'API':str})
IHS_data = pd.read_csv("IHS_data.csv",dtype={'API':str})
# fixing the APIs
Harmony_data["API"] = Harmony_data["API"].apply(fixAPI)
IHS_data["API"] = IHS_data["API"].apply(fixAPI)

In [13]:
# making an initial set of training features with the Harmony data only
temp2 = pd.merge(y_train,Harmony_data,on='API',how = 'left')
temp2.fillna(0,inplace = True)
temp2

API  Liquid  LATERAL_LENGTH_BLEND  PROP_PER_FOOT  \
0     05001097720000   65412                  4358       760.4881   
1     05001097780100   84043                  4208       611.6503   
2     05001097800000   13471                  3983         0.0000   
3     05001097820000   12992                  4221       801.2611   
4     05001097830000   15195                  4027         0.0000   
5     05001098050100  176206                  8190      1408.8110   
6     05001098450000  180189                  4315         0.0000   
7     05005071800000  126323                  4053      3401.1990   
8     05005071890100   66150                  3745      1742.2890   
9     05005071920000  186252                  3866      1835.5640   
10    05005072090000  142882                  4079      1568.7120   
11    05005072120000   62652                  3262      1914.9830   
12    05005072140100   63836                  3841      1738.0710   
13    05005072150100   99022                  3787         0.0000   
14    05005072170100  234552                  9005       994.6866   
15    05005072190100  264294                  6720      1876.9140   
16    05005072210000  250013                  8545      1252.0050   
17    05005072220000  102986                  3815      1876.9190   
18    05005072250100  200616                  6440       875.3403   
19    05005072260000  217756                  8540      1369.7750   
20    05123315730000   20563                  3554      1365.6510   
21    05123331840000   17377                  4012         0.0000   
22    05123334240100   20788                  3508       834.5635   
23    05123349460000   91506                  4589       221.6403   
24    05123349600000   76262                  4173       782.5092   
25    05123349910100    7703                  2550         0.0000   
26    05123350610000   70095                  4105      1178.6280   
27    05123350770000   91265                  4038       651.1269   
28    05123352460000   28831                  8813       875.0183   
29    05123352590000   51454                  3902         0.0000   
...              ...     ...                   ...            ...   
7814  49021211170000  180118                  9434       646.8029   
7815  49021211180000  133436                  9678       639.8415   
7816  49021211280000  142229                  8897      1316.9290   
7817  49021211310000  201533                  9341      1312.9230   
7818  49021211320000   87110                  9642       613.0061   
7819  49021211460000   73927                  6647      1172.1610   
7820  49021211760000   31937                  4059      1198.5090   
7821  49021211780000  207008                  9014      1350.5770   
7822  49021211800000  236270                  9445      1296.2060   
7823  49021211820000  191163                  8930      1398.2330   
7824  49021212030000  146182                  9457      1307.2390   
7825  49021212280000  164647                  9480      1077.4830   
7826  49021212460000  222063                  8971      2424.1120   
7827  49021212470000  187938                  8627      2391.5970   
7828  49021212490000  236922                  9382      2143.3760   
7829  49021213620000   95972                  9710       562.3441   
7830  49021213990000   90304                  9684       584.5623   
7831  49021214000000   31496                  4714       552.4348   
7832  49021214010000   41765                  4779       266.3333   
7833  49021215910000   88956                  9784       543.0637   
7834  49021217890000   63698                  1659       522.7615   
7835  49021219480000  134031                  9705      1297.6180   
7836  49021221450000  161373                  9670       437.8219   
7837  49021222690000  106619                  9822       572.4443   
7838  49021222710000   71089                  9527       622.4385   
7839  49021222940000  227454                 10138      2534.0880   
7840  490212229

In [14]:
x_train = temp2.drop(['API','Liquid'], axis=1)
x_train

LATERAL_LENGTH_BLEND  PROP_PER_FOOT  WATER_PER_FOOT       GOR_30  \
0                     4358       760.4881        934.0413  2841.940260   
1                     4208       611.6503        546.6923  2420.241440   
2                     3983         0.0000          0.0000  2076.526858   
3                     4221       801.2611        505.2079  3652.173913   
4                     4027         0.0000          0.0000  2457.326098   
5                     8190      1408.8110          0.0000  1598.716588   
6                     4315         0.0000          0.0000  1407.787232   
7                     4053      3401.1990       2065.5310  1216.537860   
8                     3745      1742.2890       1807.3310  2059.910523   
9                     3866      1835.5640       1890.1990  3186.014597   
10                    4079      1568.7120       1630.7050  1654.373024   
11                    3262      1914.9830       1672.1780  2018.015596   
12                    3841      1738.0710       1281.4290  1905.849582   
13                    3787         0.0000          0.0000  1322.132647   
14                    9005       994.6866        591.8004  1249.318351   
15                    6720      1876.9140       1618.9850  1214.378209   
16                    8545      1252.0050       1235.5770  1061.961113   
17                    3815      1876.9190       1047.6740  1308.664642   
18                    6440       875.3403       1035.7760  2729.685603   
19                    8540      1369.7750       1313.5470  2009.318579   
20                    3554      1365.6510       1012.7990   498.804543   
21                    4012         0.0000          0.0000  3247.303236   
22                    3508       834.5635        651.6735  3074.136764   
23                    4589       221.6403        131.7694  2099.389996   
24                    4173       782.5092        594.7244  3173.713704   
25                    2550         0.0000        801.4464   605.031447   
26                    4105      1178.6280        807.1788  1976.423416   
27                    4038       651.1269        526.2178  2034.171413   
28                    8813       875.0183        464.8092  3757.302405   
29                    3902         0.0000          0.0000  3007.571259   
...                    ...            ...             ...          ...   
7814                  9434       646.8029          0.0000   330.741734   
7815                  9678       639.8415          0.0000   418.323704   
7816                  8897      1316.9290        662.2171   607.470289   
7817                  9341      1312.9230        849.5093   694.357309   
7818                  9642       613.0061          0.0000   569.349788   
7819                  6647      1172.1610        674.7793  1139.989029   
7820                  4059      1198.5090          0.0000   692.955112   
7821                  9014      1350.5770        838.8643   809.819371   
7822                  9445      1296.2060        812.3987  1169.257483   
7823                  8930      1398.2330        879.5729   495.476819   
7824                  9457      1307.2390        835.6952   843.114626   
7825                  9480      1077.4830        847.9736   611.024075   
7826                  8971      2424.1120       1348.6120   609.965988   
7827                  8627      2391.5970       1441.0970   454.680978   
7828                  9382      2143.3760       1241.4700   609.038127   
7829                  9710       562.3441          0.0000   534.401136   
7830                  9684       584.5623          0.0000   556.290893   
7831                  4714       552.4348          0.0000   543.292103   
7832                  4779       266.3333          0.0000   397.645115   
7833                  9784       543.0637          0.0000   587.270156   
7834                  1659       522.7615          0.0000   495.260664   
7835                  9705      1297.6180        876.0724   674.773118   
7836      

In [15]:
x_train = np.array(x_train)
y_train = np.array(y_train) 
y_train.shape
x_train.shape
print(x_train.shape,y_train.shape)

(7844, 6) (7844, 1)


In [16]:
# normalize training data
# x_train = sk.normalize(x_train)
x_train

array([[4358.        ,  760.4881    ,  934.0413    , 2841.94025951,
        3126.39585693, 3270.49944883],
       [4208.        ,  611.6503    ,  546.6923    , 2420.24143953,
        2878.66692315, 2799.40106766],
       [3983.        ,    0.        ,    0.        , 2076.52685798,
        1289.76123027,  936.7157665 ],
       ...,
       [8161.        , 2202.056     , 1387.139     ,  542.96133666,
         472.57393067,  517.34242223],
       [4208.        ,  584.2202    ,  217.9879    ,  416.33986928,
         405.864774  ,  366.30466686],
       [4249.        ,  538.438     ,    0.        ,  355.67514677,
         410.45096636,  464.87159181]])

In [40]:
# creating the Machine Learning model
model = Sequential()
model.add(Dense(output_dim=4, activation=LeakyReLU(alpha=0.3), input_dim=x_train.shape[1]))
# model.add(Dense(output_dim=4, activation=LeakyReLU(alpha=0.3)))
model.add(Dense(output_dim=y_train.shape[1], activation='linear'))
adam = Adam(lr=0.1)
model.compile(loss='mae', optimizer=adam)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation=<keras.lay..., input_dim=6, units=4)`
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:5: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="linear", units=1)`
  """


In [41]:
# fitting the model
model.fit(x_train,y_train,batch_size = 512, epochs= 20000 , verbose = 1,shuffle = True)

Epoch 1/20000
7844/7844 [==============================] - 0s 32us/step - loss: 104778.0182
Epoch 2/20000
7844/7844 [==============================] - 0s 2us/step - loss: 59465.9054
Epoch 3/20000
7844/7844 [==============================] - 0s 2us/step - loss: 52908.9886
Epoch 4/20000
7844/7844 [==============================] - 0s 2us/step - loss: 51379.8496
Epoch 5/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50998.1037
Epoch 6/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50686.4030
Epoch 7/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50705.7062
Epoch 8/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50650.3823
Epoch 9/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50820.9538
Epoch 10/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50860.9768
Epoch 11/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50678.7742
Epoch 

7844/7844 [==============================] - 0s 1us/step - loss: 50814.4549
Epoch 92/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50834.4421
Epoch 93/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50544.9886
Epoch 94/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50854.3140
Epoch 95/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50757.8117
Epoch 96/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50596.1213
Epoch 97/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50581.3684
Epoch 98/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50581.5017
Epoch 99/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50583.8534
Epoch 100/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50532.2215
Epoch 101/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50545.3023
Epoch 102/20

7844/7844 [==============================] - 0s 1us/step - loss: 50234.1262
Epoch 270/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50213.6568
Epoch 271/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50102.9611
Epoch 272/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50331.4518
Epoch 273/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50281.6324
Epoch 274/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50320.8415
Epoch 275/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50542.2528
Epoch 276/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50209.3340
Epoch 277/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50422.7294
Epoch 278/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50194.1744
Epoch 279/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50260.3208
Epoc

7844/7844 [==============================] - 0s 1us/step - loss: 50315.0993
Epoch 448/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50039.6881
Epoch 449/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50022.1408
Epoch 450/20000
7844/7844 [==============================] - 0s 2us/step - loss: 50039.6046
Epoch 451/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49912.8458
Epoch 452/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50244.3081
Epoch 453/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50071.7110
Epoch 454/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50152.9064
Epoch 455/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50068.2909
Epoch 456/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50127.8479
Epoch 457/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50035.2381
Epoc

7844/7844 [==============================] - 0s 1us/step - loss: 49972.7372
Epoch 626/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49977.7132
Epoch 627/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50016.4571
Epoch 628/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49951.8160
Epoch 629/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49996.0275
Epoch 630/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50079.1089
Epoch 631/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50081.8883
Epoch 632/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50009.3890
Epoch 633/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50137.6500
Epoch 634/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50101.1763
Epoch 635/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50185.1556
Epoc

...

7844/7844 [==============================] - 0s 1us/step - loss: 49529.8610
Epoch 19179/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49667.0002
Epoch 19180/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49601.5267
Epoch 19181/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49350.8618
Epoch 19182/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49572.8149
Epoch 19183/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49539.3698
Epoch 19184/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49325.8122
Epoch 19185/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49270.6363
Epoch 19186/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49137.3056
Epoch 19187/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49318.8720
Epoch 19188/20000
7844/7844 [==============================] - 0s 1us/step - l

7844/7844 [==============================] - 0s 1us/step - loss: 49796.8992
Epoch 19353/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50750.4759
Epoch 19354/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49267.7026
Epoch 19355/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49203.1828
Epoch 19356/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49503.7411
Epoch 19357/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49437.3648
Epoch 19358/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49479.8822
Epoch 19359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49572.6591
Epoch 19360/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49989.2844
Epoch 19361/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49483.7550
Epoch 19362/20000
7844/7844 [==============================] - 0s 1us/step - l

7844/7844 [==============================] - 0s 1us/step - loss: 49232.2771
Epoch 19527/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49188.3588
Epoch 19528/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49146.9407
Epoch 19529/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49377.8899
Epoch 19530/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49499.5782
Epoch 19531/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49654.8453
Epoch 19532/20000
7844/7844 [==============================] - 0s 1us/step - loss: 50039.0862
Epoch 19533/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49275.1250
Epoch 19534/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49588.6130
Epoch 19535/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49331.4349
Epoch 19536/20000
7844/7844 [==============================] - 0s 1us/step - l

7844/7844 [==============================] - 0s 1us/step - loss: 49630.3209
Epoch 19701/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49422.9777
Epoch 19702/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49229.3096
Epoch 19703/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49221.9530
Epoch 19704/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49395.1608
Epoch 19705/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49605.5098
Epoch 19706/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49294.5250
Epoch 19707/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49552.8770
Epoch 19708/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49662.3290
Epoch 19709/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49180.1152
Epoch 19710/20000
7844/7844 [==============================] - 0s 1us/step - l

7844/7844 [==============================] - 0s 1us/step - loss: 49481.6888
Epoch 19875/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49228.2323
Epoch 19876/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49380.3393
Epoch 19877/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49259.7178
Epoch 19878/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49112.5142
Epoch 19879/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49916.4246
Epoch 19880/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49493.4713
Epoch 19881/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49200.2096
Epoch 19882/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49203.5039
Epoch 19883/20000
7844/7844 [==============================] - 0s 1us/step - loss: 49314.5372
Epoch 19884/20000
7844/7844 [==============================] - 0s 1us/step - l

In [17]:
# getting features from the IHS_data
temp3 = IHS_data.drop(['PermitDate','SpudDate','CompletionDate','FirstProductionDate'], axis=1)
temp3

API                      operatorNameIHS  \
0      33061020640000   CONTINENTAL RESOURCES INCORPORATED   
1      25083228390000              XTO ENERGY INCORPORATED   
2      25083231000000                 KRAKEN OPERATING LLC   
3      33053032050000       BURLINGTON RESOURCES O&G CO LP   
4      25083228880100   CONTINENTAL RESOURCES INCORPORATED   
5      33053031440000   CONTINENTAL RESOURCES INCORPORATED   
6      33025023360000             WPX ENERGY WILLISTON LLC   
7      33023006690000   CONTINENTAL RESOURCES INCORPORATED   
8      33013015390000           EOG RESOURCES INCORPORATED   
9      33025012270000                     HUNT OIL COMPANY   
10     33023006700000   CONTINENTAL RESOURCES INCORPORATED   
11     25085218680000           EOG RESOURCES INCORPORATED   
12     33061016590000           EOG RESOURCES INCORPORATED   
13     33105020500100   CONTINENTAL RESOURCES INCORPORATED   
14     33105018960000           EOG RESOURCES INCORPORATED   
15     33053063280000                    EQUINOR ENERGY LP   
16     33053032540000   CONTINENTAL RESOURCES INCORPORATED   
17     33055001750000             WPX ENERGY WILLISTON LLC   
18     33105020810000           EOG RESOURCES INCORPORATED   
19     25083228990000   CONTINENTAL RESOURCES INCORPORATED   
20     25083231090000   CONTINENTAL RESOURCES INCORPORATED   
21     25083231910000   CONTINENTAL RESOURCES INCORPORATED   
22     33061011010000           EOG RESOURCES INCORPORATED   
23     33023006610000   CONTINENTAL RESOURCES INCORPORATED   
24     33025012640000   CONTINENTAL RESOURCES INCORPORATED   
25     33061014200000                     HUNT OIL COMPANY   
26     33007016630000   CONTINENTAL RESOURCES INCORPORATED   
27     25083228310000           EOG RESOURCES INCORPORATED   
28     33061013910000               RAMPART ENERGY COMPANY   
29     33053061700000                       PETRO-HUNT LLC   
...               ...                                  ...   
48935  33053080160100    OASIS PETROLEUM NORTH AMERICA LLC   
48936  42389370910000                 CENTENNIAL RESOURCES   
48937  42475373790200         FELIX ENERGY HOLDINGS II LLC   
48938  42227396070000                  SURGE OPERATING LLC   
48939  42329424940000              MURCHISON OIL & GAS LLC   
48940  42461408670000  ENCANA OIL & GAS (USA) INCORPORATED   
48941  42461408690000  ENCANA OIL & GAS (USA) INCORPORATED   
48942  42475372330100  SHELL WESTERN E & P INCORPORATED LP   
48943  42227396260000                  SURGE OPERATING LLC   
48944  42301340140000       HEADINGTON ENERGY PARTNERS LLC   
48945  42389371540000            NOBLE ENERGY INCORPORATED   
48946  42329422560200  ENCANA OIL & GAS (USA) INCORPORATED   
48947  42301331460100           EOG RESOURCES INCORPORATED   
48948  30015449720000                MEWBOURNE OIL COMPANY   
48949  42371397530000               JAGGED PEAK ENERGY LLC   
48950  42389371720000                       OXY USA WTP LP   
48951  42371395510100                    GORDY OIL COMPANY   
48952  33025033360100             WPX ENERGY WILLISTON LLC   
48953  35049252030000       RIMROCK RESOURCE OPERATING LLC   
48954  42227396450000                  SURGE OPERATING LLC   
48955  30025449040000           EOG RESOURCES INCORPORATED   
48956  35017252380000         PALOMA OPERATING COMPANY INC   
48957  42383403290000             EARTHSTONE OPERATING LLC   
48958  42329422110100                   APACHE CORPORATION   
48959  42461406570100    PIONEER NATURAL RESOURCES USA INC   
48960  42475374150300               JAGGED PEAK ENERGY LLC   
48961  42475375400100           CALLON PETROLEUM OPERATING   
48962  30015446810100        CHISHOLM ENERGY OPERATING LLC   
48963  42301338440100            WPX ENERGY PRODUCTION LLC   
48964  33105046000100                 KRAKEN OPERATING LLC   

                      formation        BasinName     StateName CountyName  \
0                        BAKKEN  WILLISTON BASIN  NORTH DAKOTA  MOUNTRAIL   
1                  

In [18]:
d = {}
i = 0
for name in temp3.operatorNameIHS.unique():
    d[name] = i
    i += 1
temp3.replace({'operatorNameIHS': d},inplace = True)

d = {}
i = 0
for name in temp3.formation.unique():
    d[name] = i
    i += 1
temp3.replace({'formation': d},inplace = True)

d = {}
i = 0
for name in temp3.BasinName.unique():
    d[name] = i
    i += 1
temp3.replace({'BasinName': d},inplace = True)

d = {}
i = 0
for name in temp3.StateName.unique():
    d[name] = i
    i += 1
temp3.replace({'StateName': d},inplace = True)

d = {}
i = 0
for name in temp3.CountyName.unique():
    d[name] = i
    i += 1
temp3.replace({'CountyName': d},inplace = True)
temp3

API  operatorNameIHS  formation  BasinName  StateName  \
0      33061020640000                0          0          0          0   
1      25083228390000                1          0          0          1   
2      25083231000000                2          0          0          1   
3      33053032050000                3          0          0          0   
4      25083228880100                0          0          0          1   
5      33053031440000                0          0          0          0   
6      33025023360000                4          0          0          0   
7      33023006690000                0          0          0          0   
8      33013015390000                5          0          0          0   
9      33025012270000                6          0          0          0   
10     33023006700000                0          0          0          0   
11     25085218680000                5          0          0          1   
12     33061016590000                5          0          0          0   
13     33105020500100                0          0          0          0   
14     33105018960000                5          0          0          0   
15     33053063280000                7          0          0          0   
16     33053032540000                0          0          0          0   
17     33055001750000                4          0          0          0   
18     33105020810000                5          0          0          0   
19     25083228990000                0          0          0          1   
20     25083231090000                0          0          0          1   
21     25083231910000                0          0          0          1   
22     33061011010000                5          0          0          0   
23     33023006610000                0          0          0          0   
24     33025012640000                0          0          0          0   
25     33061014200000                6          0          0          0   
26     33007016630000                0          0          0          0   
27     25083228310000                5          0          0          1   
28     33061013910000                8          0          0          0   
29     33053061700000                9          0          0          0   
...               ...              ...        ...        ...        ...   
48935  33053080160100               12         27          0          0   
48936  42389370910000               97        216          2          4   
48937  42475373790200               71        216          2          4   
48938  42227396070000              354        171          2          4   
48939  42329424940000              544        171          2          4   
48940  42461408670000              352        171          2          4   
48941  42461408690000              352        171          2          4   
48942  42475372330100               53        216          2          4   
48943  42227396260000              354        171          2          4   
48944  42301340140000              560        216          2          4   
48945  42389371540000              154        220          2          4   
48946  42329422560200              352        171          2          4   
48947  42301331460100                5        216          2          4   
48948  30015449720000               64        216          2          3   
48949  42371397530000               83        216          2          4   
48950  42389371720000               77        220          2          4   
48951  42371395510100              568        220          2          4   
48952  33025033360100                4         27          0          0   
48953  35049252030000              473        239          1          2   
48954  42227396450000              354        171          2          4   
48955  30025449040000                5        217          2          3   
48956  35017252380000              439     

In [19]:
temp4 = pd.merge(temp2,temp3,on='API',how = 'left')
temp4

API  Liquid  LATERAL_LENGTH_BLEND  PROP_PER_FOOT  \
0     05001097720000   65412                  4358       760.4881   
1     05001097780100   84043                  4208       611.6503   
2     05001097800000   13471                  3983         0.0000   
3     05001097820000   12992                  4221       801.2611   
4     05001097830000   15195                  4027         0.0000   
5     05001098050100  176206                  8190      1408.8110   
6     05001098450000  180189                  4315         0.0000   
7     05005071800000  126323                  4053      3401.1990   
8     05005071890100   66150                  3745      1742.2890   
9     05005071920000  186252                  3866      1835.5640   
10    05005072090000  142882                  4079      1568.7120   
11    05005072120000   62652                  3262      1914.9830   
12    05005072140100   63836                  3841      1738.0710   
13    05005072150100   99022                  3787         0.0000   
14    05005072170100  234552                  9005       994.6866   
15    05005072190100  264294                  6720      1876.9140   
16    05005072210000  250013                  8545      1252.0050   
17    05005072220000  102986                  3815      1876.9190   
18    05005072250100  200616                  6440       875.3403   
19    05005072260000  217756                  8540      1369.7750   
20    05123315730000   20563                  3554      1365.6510   
21    05123331840000   17377                  4012         0.0000   
22    05123334240100   20788                  3508       834.5635   
23    05123349460000   91506                  4589       221.6403   
24    05123349600000   76262                  4173       782.5092   
25    05123349910100    7703                  2550         0.0000   
26    05123350610000   70095                  4105      1178.6280   
27    05123350770000   91265                  4038       651.1269   
28    05123352460000   28831                  8813       875.0183   
29    05123352590000   51454                  3902         0.0000   
...              ...     ...                   ...            ...   
7814  49021211170000  180118                  9434       646.8029   
7815  49021211180000  133436                  9678       639.8415   
7816  49021211280000  142229                  8897      1316.9290   
7817  49021211310000  201533                  9341      1312.9230   
7818  49021211320000   87110                  9642       613.0061   
7819  49021211460000   73927                  6647      1172.1610   
7820  49021211760000   31937                  4059      1198.5090   
7821  49021211780000  207008                  9014      1350.5770   
7822  49021211800000  236270                  9445      1296.2060   
7823  49021211820000  191163                  8930      1398.2330   
7824  49021212030000  146182                  9457      1307.2390   
7825  49021212280000  164647                  9480      1077.4830   
7826  49021212460000  222063                  8971      2424.1120   
7827  49021212470000  187938                  8627      2391.5970   
7828  49021212490000  236922                  9382      2143.3760   
7829  49021213620000   95972                  9710       562.3441   
7830  49021213990000   90304                  9684       584.5623   
7831  49021214000000   31496                  4714       552.4348   
7832  49021214010000   41765                  4779       266.3333   
7833  49021215910000   88956                  9784       543.0637   
7834  49021217890000   63698                  1659       522.7615   
7835  49021219480000  134031                  9705      1297.6180   
7836  49021221450000  161373                  9670       437.8219   
7837  49021222690000  106619                  9822       572.4443   
7838  49021222710000   71089                  9527       622.4385   
7839  49021222940000  227454                 10138      2534.0880   
7840  490212229

In [20]:
x_train_new = temp4.drop(['API','Liquid'], axis=1)
x_train_new

LATERAL_LENGTH_BLEND  PROP_PER_FOOT  WATER_PER_FOOT       GOR_30  \
0                     4358       760.4881        934.0413  2841.940260   
1                     4208       611.6503        546.6923  2420.241440   
2                     3983         0.0000          0.0000  2076.526858   
3                     4221       801.2611        505.2079  3652.173913   
4                     4027         0.0000          0.0000  2457.326098   
5                     8190      1408.8110          0.0000  1598.716588   
6                     4315         0.0000          0.0000  1407.787232   
7                     4053      3401.1990       2065.5310  1216.537860   
8                     3745      1742.2890       1807.3310  2059.910523   
9                     3866      1835.5640       1890.1990  3186.014597   
10                    4079      1568.7120       1630.7050  1654.373024   
11                    3262      1914.9830       1672.1780  2018.015596   
12                    3841      1738.0710       1281.4290  1905.849582   
13                    3787         0.0000          0.0000  1322.132647   
14                    9005       994.6866        591.8004  1249.318351   
15                    6720      1876.9140       1618.9850  1214.378209   
16                    8545      1252.0050       1235.5770  1061.961113   
17                    3815      1876.9190       1047.6740  1308.664642   
18                    6440       875.3403       1035.7760  2729.685603   
19                    8540      1369.7750       1313.5470  2009.318579   
20                    3554      1365.6510       1012.7990   498.804543   
21                    4012         0.0000          0.0000  3247.303236   
22                    3508       834.5635        651.6735  3074.136764   
23                    4589       221.6403        131.7694  2099.389996   
24                    4173       782.5092        594.7244  3173.713704   
25                    2550         0.0000        801.4464   605.031447   
26                    4105      1178.6280        807.1788  1976.423416   
27                    4038       651.1269        526.2178  2034.171413   
28                    8813       875.0183        464.8092  3757.302405   
29                    3902         0.0000          0.0000  3007.571259   
...                    ...            ...             ...          ...   
7814                  9434       646.8029          0.0000   330.741734   
7815                  9678       639.8415          0.0000   418.323704   
7816                  8897      1316.9290        662.2171   607.470289   
7817                  9341      1312.9230        849.5093   694.357309   
7818                  9642       613.0061          0.0000   569.349788   
7819                  6647      1172.1610        674.7793  1139.989029   
7820                  4059      1198.5090          0.0000   692.955112   
7821                  9014      1350.5770        838.8643   809.819371   
7822                  9445      1296.2060        812.3987  1169.257483   
7823                  8930      1398.2330        879.5729   495.476819   
7824                  9457      1307.2390        835.6952   843.114626   
7825                  9480      1077.4830        847.9736   611.024075   
7826                  8971      2424.1120       1348.6120   609.965988   
7827                  8627      2391.5970       1441.0970   454.680978   
7828                  9382      2143.3760       1241.4700   609.038127   
7829                  9710       562.3441          0.0000   534.401136   
7830                  9684       584.5623          0.0000   556.290893   
7831                  4714       552.4348          0.0000   543.292103   
7832                  4779       266.3333          0.0000   397.645115   
7833                  9784       543.0637          0.0000   587.270156   
7834                  1659       522.7615          0.0000   495.260664   
7835                  9705      1297.6180        876.0724   674.773118   
7836      

In [21]:
x_train_new = np.array(x_train_new)
print(x_train_new.shape,y_train.shape)

(7844, 15) (7844, 1)


In [33]:
# creating new model
model = Sequential()
model.add(Dense(output_dim=10, activation=LeakyReLU(alpha=0.3), input_dim=x_train_new.shape[1]))
model.add(Dense(output_dim=5, activation=LeakyReLU(alpha=0.3)))
model.add(Dense(output_dim=3, activation=LeakyReLU(alpha=0.3)))
model.add(Dense(output_dim=y_train.shape[1], activation='linear'))
adam = Adam(lr=0.001)
model.compile(loss='mae', optimizer=adam)

c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation=<keras.lay..., input_dim=15, units=10)`
  This is separate from the ipykernel package so we can avoid doing imports until
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:4: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation=<keras.lay..., units=5)`
  after removing the cwd from sys.path.
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:5: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation=<keras.lay..., units=3)`
  """
c:\users\gigabyte\appdata\local\programs\python\python37\lib\site-packages\ipykernel_launcher.py:6: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="linear", units=1)`
  


In [34]:
# fitting the model
model.fit(x_train_new,y_train,batch_size = 512, epochs= 20000 , verbose = 1,shuffle = True)

Epoch 1/20000
7844/7844 [==============================] - 0s 30us/step - loss: 128518.8460
Epoch 2/20000
7844/7844 [==============================] - 0s 2us/step - loss: 127692.2131
Epoch 3/20000
7844/7844 [==============================] - 0s 2us/step - loss: 126949.6119
Epoch 4/20000
7844/7844 [==============================] - 0s 2us/step - loss: 126409.1051
Epoch 5/20000
7844/7844 [==============================] - 0s 2us/step - loss: 125795.0398
Epoch 6/20000
7844/7844 [==============================] - 0s 2us/step - loss: 125087.2901
Epoch 7/20000
7844/7844 [==============================] - 0s 2us/step - loss: 124220.4761
Epoch 8/20000
7844/7844 [==============================] - 0s 2us/step - loss: 123167.2785
Epoch 9/20000
7844/7844 [==============================] - 0s 2us/step - loss: 121909.3463
Epoch 10/20000
7844/7844 [==============================] - 0s 2us/step - loss: 120327.9485
Epoch 11/20000
7844/7844 [==============================] - 0s 2us/step - loss: 118394.9

Epoch 91/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49875.4845
Epoch 92/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49860.0309
Epoch 93/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49847.7866
Epoch 94/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49830.7772
Epoch 95/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49825.0194
Epoch 96/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49799.9510
Epoch 97/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49779.6338
Epoch 98/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49765.9864
Epoch 99/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49750.1345
Epoch 100/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49733.0034
Epoch 101/20000
7844/7844 [==============================] - 0s 2us/step - loss: 49714.09

7844/7844 [==============================] - 0s 2us/step - loss: 48506.2487
Epoch 180/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48462.5730
Epoch 181/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48440.2052
Epoch 182/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48422.7221
Epoch 183/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48412.3019
Epoch 184/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48390.4333
Epoch 185/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48378.2465
Epoch 186/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48363.3608
Epoch 187/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48343.0797
Epoch 188/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48331.3766
Epoch 189/20000
7844/7844 [==============================] - 0s 2us/step - loss: 48316.3656
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 47304.4559
Epoch 269/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47314.6194
Epoch 270/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47279.6285
Epoch 271/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47301.8927
Epoch 272/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47265.1565
Epoch 273/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47252.6868
Epoch 274/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47244.6007
Epoch 275/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47235.7771
Epoch 276/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47231.0153
Epoch 277/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47244.5208
Epoch 278/20000
7844/7844 [==============================] - 0s 2us/step - loss: 47236.8829
Epoc

7844/7844 [==============================] - 0s 2us/step - loss: 46852.3144
Epoch 358/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46864.8963
Epoch 359/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46820.5914
Epoch 360/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46817.8549
Epoch 361/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46834.4718
Epoch 362/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46864.1358
Epoch 363/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46848.5792
Epoch 364/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46829.2431
Epoch 365/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46875.8339
Epoch 366/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46809.1635
Epoch 367/20000
7844/7844 [==============================] - 0s 2us/step - loss: 46784.8338
Epoc

...

7844/7844 [==============================] - 0s 2us/step - loss: 41154.7621
Epoch 19613/20000
7844/7844 [==============================] - 0s 3us/step - loss: 41356.3413
Epoch 19614/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41270.1028
Epoch 19615/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41313.0671
Epoch 19616/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41100.6242
Epoch 19617/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41114.8632
Epoch 19618/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41356.6490
Epoch 19619/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41147.0069
Epoch 19620/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41099.3560
Epoch 19621/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41097.5639
Epoch 19622/20000
7844/7844 [==============================] - 0s 2us/step - l

7844/7844 [==============================] - 0s 3us/step - loss: 41125.2884
Epoch 19700/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41169.9621
Epoch 19701/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41072.7477
Epoch 19702/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41198.1786
Epoch 19703/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41417.7002
Epoch 19704/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41205.4171
Epoch 19705/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41166.0050
Epoch 19706/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41177.9968
Epoch 19707/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41228.6451
Epoch 19708/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41116.5883
Epoch 19709/20000
7844/7844 [==============================] - 0s 2us/step - l

7844/7844 [==============================] - 0s 2us/step - loss: 41441.2639
Epoch 19787/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41166.6566
Epoch 19788/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41202.6262
Epoch 19789/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41100.7157
Epoch 19790/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41151.3725
Epoch 19791/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41192.9901
Epoch 19792/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41195.6663
Epoch 19793/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41188.5986
Epoch 19794/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41357.0193
Epoch 19795/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41314.0018
Epoch 19796/20000
7844/7844 [==============================] - 0s 2us/step - l

7844/7844 [==============================] - 0s 2us/step - loss: 41191.8574
Epoch 19874/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41132.2289
Epoch 19875/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41143.6460
Epoch 19876/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41145.6743
Epoch 19877/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41094.5862
Epoch 19878/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41099.7057
Epoch 19879/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41094.9515
Epoch 19880/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41138.9221
Epoch 19881/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41116.4581
Epoch 19882/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41156.9134
Epoch 19883/20000
7844/7844 [==============================] - 0s 2us/step - l

7844/7844 [==============================] - 0s 2us/step - loss: 41326.8428
Epoch 19961/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41098.5545
Epoch 19962/20000
7844/7844 [==============================] - 0s 3us/step - loss: 41153.5462
Epoch 19963/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41193.2789
Epoch 19964/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41260.9614
Epoch 19965/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41310.0351
Epoch 19966/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41178.9254
Epoch 19967/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41175.5163
Epoch 19968/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41157.7535
Epoch 19969/20000
7844/7844 [==============================] - 0s 2us/step - loss: 41101.0942
Epoch 19970/20000
7844/7844 [==============================] - 0s 2us/step - l